In [12]:
import os
import pandas as pd
import numpy as np
from google.colab import drive
from IPython.display import clear_output

drive.mount('/content/gdrive')

code_folder = '/content/gdrive/MyDrive/AI Music Visuals Share/New Codes'
output_basedir = os.path.join(code_folder, 'output_transitions')

fp = os.path.join(code_folder, 'prompts_excel.xlsx')
df_prompt = pd.read_excel(fp, 'prompts', index_col=0)
df_transitions = pd.read_excel(fp, 'transitions', dtype={'from_seed': str, 'to_seed': str})

df_transitions = df_transitions.where(df_transitions['compute'] == 'y').dropna(how='all')
df_transitions

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


from_name         from_seed               to_name  \
3           alien dunes3  7658447770572237          alien dunes4   
4           alien dunes4  4548547956872502          alien dunes2   
7        far away land11  4602827649242753       far away land11   
8        far away land11  6801581842848785     overgrown fantasy   
9      overgrown fantasy  8235966877828325        far away land8   
10        far away land8  6098474812353869        alien mountain   
11        alien mountain  7285707432238947             red cave2   
12             red cave2  1488523408897636             red cave2   
13             red cave2  6196330219215539             red cave1   
14             red cave1  4940561922459094             red cave2   
15             red cave2  6196330219215539             red cave1   
16             red cave1  4866412378884770             vine cave   
17             vine cave  7078380737840840         fractal vines   
18         fractal vines  2770623383884112         fractal vines   
19         fractal vines  2597635566234304         fractal vines   
20         fractal vines  7102762937299441         fractal vines   
21         fractal vines  8819628306543445  rainbow spiral wave5   
22  rainbow spiral wave5  1727166619442474  rainbow spiral wave5   
23  rainbow spiral wave5  3116810869144921  rainbow spiral wave5   
24  rainbow spiral wave5  1289113595635541  rainbow spiral wave5   
25  rainbow spiral wave5  4476547043696287  rainbow spiral wave5   
26  rainbow spiral wave5  6527887459499496       far away land12   
27       far away land12  7534793135833247       far away land11   
28       far away land11  5383006964566936       far away land11   
29       far away land11  5640233151898680       far away land11   
30       far away land11  6408941496116634       far away land11   
31       far away land11  7534793135833247       far away land11   

             to_seed compute  duration  
3   4548547956872502       y       5.0  
4   4548547956872502       y       5.0  
7   6801581842848785       y       5.0  
8   8235966877828325       y       5.0  
9   6098474812353869       y       5.0  
10  7285707432238947       y       5.0  
11  1488523408897636       y       5.0  
12  6196330219215539       y       5.0  
13  4940561922459094       y       5.0  
14  6196330219215539       y       5.0  
15  4866412378884770       y       5.0  
16  7078380737840840       y       5.0  
17  2770623383884112       y       5.0  
18  2597635566234304       y       5.0  
19  7102762937299441       y       5.0  
20  8819628306543445       y       5.0  
21  1727166619442474       y       5.0  
22  3116810869144921       y       5.0  
23  1289113595635541       y       5.0  
24  4476547043696287       y       5.0  
25  6527887459499496       y       5.0  
26  7534793135833247       y       5.0  
27  5383006964566936       y       5.0  
28  5640233151898680       y       5.0  
29  6408941496116634       y       5.0  
30  7534793135833247       y       5.0  
31   905488377057695       y       5.0

In [4]:
%%capture
!pip install diffusers
!pip install transformers scipy ftfy accelerate

!pip install -U --no-deps stable_diffusion_videos # stable_diffusion_videos wants old version of diffusers which doesn't allow for text embeddings
!pip install realesrgan av

from stable_diffusion_videos import make_video_pyav

import torch
from diffusers import StableDiffusionPipeline

In [5]:
pipe = StableDiffusionPipeline.from_pretrained("CompVis/stable-diffusion-v1-4",
                                               torch_dtype=torch.float16,
                                               safety_checker=None
                                               )  


pipe = pipe.to("cuda")

Fetching 16 files:   0%|          | 0/16 [00:00<?, ?it/s]

/usr/local/lib/python3.8/dist-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(


In [6]:
width = 512
height = 512

latent_width = width // 8
latent_height = height // 8


def generate_latent(generator, seed, device='cuda'):

    generator.manual_seed(int(seed))

    latent = torch.randn(
        (1, pipe.unet.in_channels, height // 8, width // 8),
        generator = generator,
        device = device
    )

    return latent

def make_latent_steps(start_latent, stop_latent, steps):
    delta_latent = (stop_latent - start_latent)/steps
    latent_steps = [start_latent + delta_latent*i for i in range(steps + 1)]

    #Check that start and end values are equal to targets within rounding errors
    # assert torch.isclose(latent_steps[0], from_latent, atol=1e-4).all()
    # assert torch.isclose(latent_steps[-1], to_latent, atol=1e-2).all()

    return latent_steps

def get_text_embed(prompt):
    text_input = pipe.tokenizer(
                prompt,
                padding="max_length",
                max_length=pipe.tokenizer.model_max_length,
                truncation=True,
                return_tensors="pt",
            )

    embed = pipe.text_encoder(text_input.input_ids.to('cuda'))[0]

    return embed

if not os.path.exists(output_basedir): os.makedirs(output_basedir)

In [7]:


# from_text_embed.shape
# to_text_embed.shape

In [8]:
def slerp(t, v0, v1, DOT_THRESHOLD=0.9995):
    """helper function to spherically interpolate two arrays v1 v2"""

    inputs_are_torch = isinstance(v0, torch.Tensor)
    if inputs_are_torch:
        input_device = v0.device
        v0 = v0.cpu().numpy()
        v1 = v1.cpu().numpy()

    dot = np.sum(v0 * v1 / (np.linalg.norm(v0) * np.linalg.norm(v1)))
    if np.abs(dot) > DOT_THRESHOLD:
        v2 = (1 - t) * v0 + t * v1
    else:
        theta_0 = np.arccos(dot)
        sin_theta_0 = np.sin(theta_0)
        theta_t = theta_0 * t
        sin_theta_t = np.sin(theta_t)
        s0 = np.sin(theta_0 - theta_t) / sin_theta_0
        s1 = sin_theta_t / sin_theta_0
        v2 = s0 * v0 + s1 * v1

    if inputs_are_torch:
        v2 = torch.from_numpy(v2).to(input_device)

    return v2

In [ ]:
skip_existing = False

generator = torch.Generator(device="cuda")

max_seed_characters = 4 # Take the first few numbers of the seed for the name
num_interpolation_steps = 50
num_inference_steps = 50

T = np.linspace(0.0, 1.0, num_interpolation_steps)

for i, row in df_transitions.iterrows():
  clear_output(wait=True)

  output_name = "{}-{} to {}-{}".format(
      row['from_name'],
      row['from_seed'][:max_seed_characters],
      row['to_name'],
      row['to_seed'][:max_seed_characters]
      )
  
  output_dir = os.path.join(output_basedir, output_name)

  if os.path.exists(output_dir):
      if skip_existing:
          print("{} already exists, skipping".format(output_name))
          continue
      else:
          print("{} already exists, deleting images".format(output_name))
          for fn in os.listdir(output_dir):
            os.remove(os.path.join(output_dir, fn))
  else:
      os.makedirs(output_dir)

  prompts = [
      df_prompt['prompt'][row['from_name']], 
      df_prompt['prompt'][row['to_name']]
      ]

  guidance_scales = [
      float(df_prompt['guidance_scale'][row['from_name']]),
      float(df_prompt['guidance_scale'][row['to_name']])
  ]

  seeds = [int(row['from_seed']), int(row['to_seed'])]

  duration = float(row['duration'])
  fps = num_interpolation_steps/duration

  print("fps: {}".format(fps))

  from_latent = generate_latent(generator, seeds[0])
  to_latent = generate_latent(generator, seeds[1])

  from_text_embed = get_text_embed(prompts[0])
  to_text_embed = get_text_embed(prompts[1])

  # The tensor steps are len(num_interpolation_steps) + 1
  # latent_steps = make_latent_steps(from_latent, to_latent, num_interpolation_steps)
  # embed_steps = make_latent_steps(from_text_embed, to_text_embed, num_interpolation_steps)
  guidance_steps = np.linspace(guidance_scales[0], guidance_scales[1], num_interpolation_steps + 1)


  for i, t in enumerate(T):

      print("{}: step {}".format(output_name, i))

      embeds = torch.lerp(from_text_embed, to_text_embed, t)
      # latents = torch.lerp(from_latent, to_latent, t)
      latents = slerp(float(t), from_latent, to_latent)

      with torch.autocast('cuda'):
        images = pipe(
            prompt_embeds=embeds,
            guidance_scale=guidance_steps[i],
            latents = latents,
            num_inference_steps = num_inference_steps
        )

      clear_output(wait=True)

      output_image = images.images[0]

      output_number_string = str(i).zfill(6)
      output_image.save(os.path.join(output_dir, "frame{}.png".format(output_number_string)))


  make_video_pyav(output_dir, 
                  output_filepath=os.path.join(output_basedir,  "{}.mp4".format(output_name)),
                  fps=fps
                  )

  

fractal vines-2770 to fractal vines-2597: step 24


  0%|          | 0/50 [00:00<?, ?it/s]

In [10]:
# with torch.autocast('cuda'):
#   images = pipe(
#       prompt_embeds=embed_steps[-1],
#       guidance_scale=guidance_scales[1],
#       latents = latent_steps[-1],
#   )

# images.images[0]